## ELEX 4653 Lab 2

This lab provides practice on module imports, iterators, exception, and dictionaries.

_Version 2: fixed example function f() in Question 2._

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

Define a function `myrand(x)` that imports the `random` and `math` modules, calls `random.seed(x)` and returns `math.pi` times the first value returned from `random.random()` that is greater than 0.5.

For example, `myrand(1)` should return 2.66....

#### Question 2

Define a function `pair(a,b)` where `a` and `b` are iterables of any type and any length.   Your function should return a tuple containing two-element tuples taken from pairs of values taken from successive elements of the shortest of `a` and `b`. Your function _must_ use the `zip` iterator.

For example, if the iterable `a = iter([1,2,3])` and `b = iter("abcd")` then `pair(a,b)` should return `((1, 'a'), (2, 'b'), (3, 'c'))`.

#### Question 3

Declare a function named `checkname(s)` that raises a `ValueError` exception if `s` is shorter than 3 letters or if the first letter is lower case. The exception should include the message `Invalid: s` where `s` is the string passed to the function.  _Hint: str.islower()_.

For example, `checkname('abc')` and `checkname('ab')` should raise `ValueError` exceptions with exception messages `"Invalid: abc"` and `"Invalid: ab"` respectively, but `checkname('Abc')` should not raise an exception.

#### Question 4

Write a function `check(l,f)` that takes a list of objects `l` and a function `f` and returns a list of integers with as many values as the length of `l`.  The function should call `f` with each object in `l` in order.  The list returned should contain:
* a `0` for each value in `l` which did not raise an exception, 
* a `1` for each value in `l` which raises a `ValueError` exception, or 
* a `2` for each value in `l` which raised another exception

For example, if the function `f` raises a `ValueError` exception for negative numbers, and a `ZeroDivide` exception for zero values then calling `check([1,-2,0],f)` would return `[0, 1, 2]`.  For testing, you can use the following function `f`:

```
def f(x):
    if x < 0:
        raise(ValueError)
    elif x == 0:
        raise(ZeroDivide)
    else:
        pass
```
Note that this is _not_ the function `f()` that will be passed to your function.


#### Question 5

Write a function `countvalues(d)` that takes a `dict` argument `d` and returns another dict whose keys are the _values_ in `d` and the values are the number of times each such value appears in `d`.

For example, `countvalues({1:1, 2:1, 3:4})` would return `{1:2, 4:1}`.

In [12]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    import traceback
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.search(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.search(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    
    import math
    def roundn(num, n):
        return 0 if not num else round(num, -int(math.floor(math.log10(abs(num)))) + (n - 1))

    def ch(s,n=(1,1)):
        return randwords(1,chars=s,nl=n)[0]

    import ast, inspect
    def uses(f,s):
        for t in ast.walk(ast.parse(inspect.getsource(f))):
            if isinstance(t, ast.Call):
                if isinstance(t.func, ast.Name) and t.func.id == s:
                    return True
    
    class notalist(list):
        def __getitem__(self, index):
            raise TypeError("Indexing is not allowed, use the iterator.")

    def Q(f,a,*,rounding=None):
        oa = copy.deepcopy(a)
        r = f(*a)
        r = roundn(r,rounding) if rounding else r
        return (r,f"{f.__name__}{repr(oa)} returns {repr(r)}")

    def Q1():
        return Q(myrand,(randint(1,100),),rounding=4)
        
    def Q2():
        if not uses(pair,'zip'):
            return ([],"pair() does not use the zip() iterator.")
        a = iter(notalist(randwords(randint(2,5))))
        b = iter(notalist(randwords(randint(2,5))))
        return Q(pair,(a,b))
        
    def Q3():
        f = checkname
        a = randwords(1,chars="ABCDefgh",nl=(2,3))[0]
        oa = copy.deepcopy(a)
        try:
            f(a)
            r = "raised no exception"
        except ValueError as e:
            r = f"raised ValueError exception with string '{e}'"
        except Exception as e:
            r = f"raised wrong exception: {e}"
        return (r,f"{f.__name__}({repr(oa)}) {r}")
    
    def Q4():
        def f(x):
            i = randint(0,2)
            if i == 1:
                raise ValueError
            elif i == 2:
                raise Exception
            else:
                pass
        return Q(check,(randwords(randint(2,5)),f))
            
    def Q5():
        d = dict(zip(set(randwords(randint(5,8))),[randint(0,3) for i in range(8)]))
        return Q(countvalues,({k:d[k] for k in sorted(orderkeys(d))},))

    hashvalues = '''
Zfyw8CnIK8FVMPwvwAj6wAj6wAj6wAj6wAj6wAj6
SIL8Iw1ak0LvAi9mzAsZOZ6484NyWAXjciaUuEsA
ZWWAz+Knz+KnSs+fcpoM9ADyJpAoSkONt0SxBFy6
bFPC48o5WEUwJVlJoi2P/UsPkJc7Iqxq7PX2N+Pw
Rs0AEP902VTz15nbcA4cgjaZ9qlNjtxPL23BhNX+
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                traceback.print_exc()
                err = f"Error during test {n}: {e}"               
        if testing:
           newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)